In [1]:
from sys import path
from pprint import pprint
from bunch import Bunch

path.append('/Users/loicjounot/Code/internal-tools)')
pprint(path)

['',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python35.zip',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5/plat-darwin',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5/lib-dynload',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5/site-packages/setuptools-19.6.2-py3.5.egg',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5/site-packages',
 '/Users/loicjounot/anaconda/envs/internal-tools/lib/python3.5/site-packages/IPython/extensions',
 '/Users/loicjounot/.ipython',
 '/Users/loicjounot/Code/internal-tools)']


In [2]:
pwd

'/Users/loicjounot/Code/internal-tools/sandbox'

In [5]:
from connectors.sql import WarehouseConnector
dwh = WarehouseConnector()

In [17]:
sql = """

SELECT delivery.delivery_uuid,
    delivery.order_uuid,
    event.username,
    event.event,
    event.timestamp,
    delivery.fleet_backend_name,
    delivery.source_name,
    delivery.restaurant_name,
    delivery.restaurant_city,
    delivery.driver_username,
    delivery.customer_zipcode,
    delivery.customer_raw_address,
    delivery.distance_to_customer,
    delivery.last_delivery_status,
    delivery.last_delivery_status_timestamp,
    delivery.created_at_timestamp,
    delivery.start_route_timestamp,
    delivery.requested_pickup_timestamp,
    delivery.confirmed_pickup_timestamp,
    delivery.pick_up_eta,
    delivery.delivery_at_eta,
    delivery.cancellation_reason,
    delivery.gastronomic_day,
    delivery.air_distance_to_customer,
    delivery.customer_lat,
    delivery.customer_lng,
    delivery.created_at_hour,
    delivery.fleet_display_name,
    delivery.fleet_country_code,
    delivery.fleet_country_name

FROM tableau.audit_logs as event,
    tableau.delivery_dwh as delivery

WHERE event.delivery_uuid = delivery.delivery_uuid;

"""

In [21]:
raw = Bunch() 
raw.df = dwh.execute(sql)

In [23]:
# Remove test accounts and FCs logged in under a team username
fcs = Bunch()
fcs.junk = ['team1', 'team2', 'team3', 'team4', 'test']
fcs.df = raw.df.mask(raw.df['username'].isin(fcs.junk))
fcs.df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 105738 entries, 0 to 105737
Data columns (total 30 columns):
delivery_uuid                     67422 non-null object
order_uuid                        67422 non-null object
username                          67422 non-null object
event                             67422 non-null object
timestamp                         67422 non-null datetime64[ns]
fleet_backend_name                67422 non-null object
source_name                       67422 non-null object
restaurant_name                   67422 non-null object
restaurant_city                   67422 non-null object
driver_username                   67422 non-null object
customer_zipcode                  67422 non-null object
customer_raw_address              67422 non-null object
distance_to_customer              67412 non-null float64
last_delivery_status              67422 non-null object
last_delivery_status_timestamp    67422 non-null datetime64[ns]
created_at_timestamp            

In [24]:
from bokeh.charts import Bar, output_notebook, show
output_notebook()

fcs.events_bar_chart = Bar(raw.df, 'event', agg='count', values='event', title="FC clicking events")
show(fcs.events_bar_chart)

Loading BokehJS ...

In [38]:
# Find out how many different FCs handle each delivery
unique_fcs = Bunch()
unique_fcs.df = fcs.df['username'].groupby(fcs.df['delivery_uuid']).nunique()
unique_fcs.df.head(10)

delivery_uuid
0002588c-15f0-4e23-803a-7471fa0841b9    1
000517cb-eb75-4612-a139-7d93fc191bff    1
000574de-5d9b-4ea8-a625-3ce5eec8a4a8    1
0006b90b-f115-481d-9a30-c9593100a076    1
0006f42a-4cbe-4d4a-b1bb-0bfacf1dcb8e    1
000717e5-2ea3-44f7-944e-8e3ad527add3    1
000b406d-4fe2-4689-ba26-ccc1860d971b    1
00126532-5def-48ce-b232-024b25e9d31f    1
0012b46a-de30-47cd-b297-2ec8c0924ef3    1
00168054-ad20-4761-bc3b-d750faa9872d    1
dtype: int64

In [75]:
unique_fcs.ss = unique_fcs.df.value_counts()
unique_fcs.ss.sort_index(inplace=True)
unique_fcs.ss = unique_fcs.ss / unique_fcs.ss.sum() * 100
unique_fcs.ss

1    85.433367
2    13.585504
3     0.922679
4     0.054275
6     0.004175
dtype: float64

In [87]:
from bokeh.plotting import figure, output_notebook
output_notebook()

handlers.fig = figure(plot_width=700, 
                      plot_height=700, 
                      title='How many FCs per delivery?',
                      x_axis_label='Number of FCs', 
                      y_axis_label='Frequency (%)',
                      x_range=[0,10],
                      y_range=[0, 100])

handlers.fig.circle(unique_fcs.ss.index, 
                    unique_fcs.ss.values, 
                    size=20, 
                    color="navy")

from numpy import zeros
handlers.fig.segment(x0=unique_fcs.ss.index,
                   y0=zeros(unique_fcs.ss.size),
                   x1=unique_fcs.ss.index,
                   y1=unique_fcs.ss.values, 
                   line_width=2,
                   color='navy')

show(handlers.fig)

Loading BokehJS ...

In [130]:
clicks = Bunch()
clicks.ss = fcs.df['timestamp'].groupby(fcs.df['delivery_uuid']).count()
clicks.ss = clicks.ss.value_counts()
clicks.ss.sort_index(inplace=True)
clicks.ss

1      2382
2      6129
3     11399
4      2670
5       844
6       325
7       107
8        46
9        24
10        7
11        9
12        3
13        1
14        2
18        1
25        1
54        1
59        1
dtype: int64

In [137]:
orders = Bunch()  # clicks per order
orders.ss = fcs.df['delivery_uuid'].groupby(fcs.df['order_uuid']).nunique()
orders.ss = orders.ss.value_counts()
orders.ss.sort_index(inplace=True)
orders.ss

1    22242
2      666
3      103
4       12
5        3
6        1
dtype: int64

In [142]:
orders.fig = figure(plot_width=700, 
                      plot_height=700, 
                      title='How many deliveries per order?',
                      x_axis_label='Number of deliveries', 
                      y_axis_label='Occurences',
                      x_range=[0, 8],
                      y_range=[0,25000])

orders.fig.circle(orders.ss.index, 
                    orders.ss.values, 
                    size=20, 
                    color="green")

from numpy import zeros
orders.fig.segment(x0=orders.ss.index,
                   y0=zeros(orders.ss.size),
                   x1=orders.ss.index,
                   y1=orders.ss.values, 
                   line_width=2,
                   color='green')

show(orders.fig)

In [80]:
clicks.fig = figure(plot_width=700, 
                      plot_height=700, 
                      title='How many clicks per delivery?',
                      x_axis_label='Number of clicks', 
                      y_axis_label='Occurences',
                      x_range=[0, 10],
                      y_range=[0,12000])

clicks.fig.circle(clicks.ss.index, 
                    clicks.ss.values, 
                    size=20, 
                    color="green")

from numpy import zeros
clicks.fig.segment(x0=clicks.ss.index,
                   y0=zeros(clicks.ss.size),
                   x1=clicks.ss.index,
                   y1=clicks.ss.values, 
                   line_width=2,
                   color='green')

show(clicks.fig)

In [88]:
fcs.user_bar_chart = Bar(fcs.df, 'username', agg='count', values='username', title="fleet controllers", plot_width=800)
show(fcs.user_bar_chart)

In [115]:
from numpy import to_seconds

fcs.df['delta'] = fcs.df['timestamp'] - fcs.df['created_at_timestamp']
fcs.df['delta'].apply(to_seconds).describe()

ImportError: cannot import name 'to_seconds'

In [127]:
fcs.events = fcs.df['delta'].groupby(fcs.df['event'])
fcs.df['delta'].head()

0   00:07:09.909000
1   00:53:07.536000
2   00:54:35.919000
3   00:01:26.385000
4   00:03:32.804000
Name: delta, dtype: timedelta64[ns]

In [129]:
from bokeh.charts import BoxPlot
from pandas import Timedelta

fcs.df['minutes'] = fcs.df['delta'] / Timedelta(minutes=1)
fcs.df['minutes'] = fcs.df['minutes'][fcs.df['minutes'] < 30]

fcs.boxplot = BoxPlot(
    fcs.df, 
    values='minutes', 
    label='event',
    title="Time elapsed since creation"
)

show(fcs.boxplot)

In [ ]:
from pandas import DatetimeIndex

ts = Bunch()
ts.df = fcs.df.set_index(DatetimeIndex(fcs.df['timestamp']))
ts.df = ts.df[['event', 'username']]
ts.df.head()

In [ ]:
from numpy import nan

dummy = Bunch()
dummy.df = ts.df
dummy.df['dummy'] = nan
dummy.df['dummy'].fillna(1, inplace=True)
dummy.df.head()

In [ ]:
dummy.df.tail()

In [ ]:
from pandas import period_range

hourly.period = period_range('3/2/2016', '8/2/2016', freq='H')
hourly.df = dummy.df.to_period('H')
hourly.df.iloc[20:30].head()

In [ ]:
reset = Bunch()
reset.df = ts.df.reset_index()
reset.df.head()

In [ ]:
from pandas import MultiIndex
multi.index = MultiIndex.from_tuples(dummy.df, names=['username', 'index'])
multi.head()

In [ ]:
grouped = Bunch()
grouped.df = hourly.df.reset_index()
grouped.df = grouped.df.groupby('index').count()
grouped.df.head()

In [ ]:
from bokeh.charts import TimeSeries

nkolev = Bunch()
nkolev.df = grouped.df['dummy']
#nkolev.nkolev = nkolev.df[nkolev.username == 'nkolev']
nkolev.df.head()
plot = TimeSeries(nkolev.df,x='index', y='dummy')
show(plot)

In [ ]:
fcs.values = fcs.df.username.unique()
print(fcs.values)

In [ ]:
nkolev = Bunch()
nkolev.df = fcs.df[fcs.df.username == 'nkolev']
nkolev.df.info()

In [3]:
a = {'a': 1, 'b': 2}

In [4]:
a

{'a': 1, 'b': 2}

In [5]:
a.update({'c': 3})

In [6]:
a

{'a': 1, 'b': 2, 'c': 3}